In [1]:
import sqlite3, json
from contextlib import closing

# use test.py to update questions in db!!!
def load_questions(sqlite_filename):
  all_questions = []
  with closing(sqlite3.connect(sqlite_filename)) as db:
    db.row_factory = sqlite3.Row
    with closing(db.cursor()) as cursor:
      results = cursor.execute(
        "SELECT id, articleId, title, category, section, questions FROM articles WHERE articleType = ? AND doNotUse IS NULL OR doNotUse = 0",
        ('article',)
      ).fetchall()
      
      for res in results:
        
        questions = json.loads(res['questions'])
        # questions_copy = questions.copy()
        
        for q in questions:
          q['query'] = " ".join(res['section'].split() + res['title'].split() + q['question'].split()).lower()
          q['articleId'] = res['articleId']
          
        # for q in questions_copy:
        #   q['query'] = q['question']
        #   q['articleId'] = res['articleId']

        all_questions += questions
        # all_questions += questions_copy
  return all_questions

questions = load_questions("omnidesk-ai-chatgpt-questions.sqlite")

In [2]:
from langchain.vectorstores import FAISS
from langchain.docstore.document import Document
from langchain.embeddings import SentenceTransformerEmbeddings

In [3]:
docs = [
  Document(page_content=q['query'], metadata={ 'answer': q['answer'], 'articleId': q['articleId'] })
  for q in questions
]

In [1]:
from extract_keywords import normalize_word, canonical_keywords, merge_keywords, tokenize_sentence, extract_keywords, init_keyword_extractor
#init_keyword_extractor()

In [5]:
print(tokenize_sentence('почты росии'))

['почта', 'россия']


In [3]:
embeddings = SentenceTransformerEmbeddings(model_name="multi-qa-MiniLM-L6-cos-v1")

╭─────────────────────────────── Traceback (most recent call last) ────────────────────────────────╮
│ /tmp/ipykernel_1594240/2036088539.py:1 in <module>                                               │
│                                                                                                  │
│ [Errno 2] No such file or directory: '/tmp/ipykernel_1594240/2036088539.py'                      │
╰──────────────────────────────────────────────────────────────────────────────────────────────────╯
NameError: name 'SentenceTransformerEmbeddings' is not defined

In [5]:
output_dir = 'faiss_qa'

In [7]:
db = FAISS.from_documents(docs, embeddings)
db.save_local(output_dir)

In [ ]:
%pip install faiss-cpu langchain
%pip install -U pydantic==1.10.7

In [1]:
from langchain.vectorstores import FAISS
from langchain.embeddings import SentenceTransformerEmbeddings

embeddings = SentenceTransformerEmbeddings(model_name="multi-qa-MiniLM-L6-cos-v1")
db = FAISS.load_local('faiss_qa', embeddings)

/home/makcrx/anaconda3/lib/python3.10/site-packages/deeplake/util/check_latest_version.py:32: UserWarning: A newer version of deeplake (3.6.15) is available. It's recommended that you update to the latest version using `pip install -U deeplake`.
  warnings.warn(
2023-08-03 23:36:22.968666: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


In [7]:
query = 'Почему у триггеров Почт России симваольный код не тот?'
result_docs = db.similarity_search_with_score(query, k=20)

In [8]:
import reranking

sentences = [doc[0].page_content for doc in result_docs]
score, index = reranking.search(query, sentences)

In [16]:
result_docs[index][0].metadata['answer']

'Символьный код доставки Почта России - russian-post.'

In [17]:
import gradio as gr
import reranking

def main(query):
    result_docs = db.similarity_search_with_score(query, k=20)
    sentences = [doc[0].page_content for doc in result_docs]
    score, index = reranking.search(query, sentences)
    return result_docs[index][0].metadata['answer']

demo = gr.Interface(fn=main, inputs="text", outputs="text")

demo.launch()

Exception in thread Thread-9 (run):
Traceback (most recent call last):
  File "/home/makcrx/anaconda3/lib/python3.10/site-packages/nest_asyncio.py", line 27, in run
    loop = asyncio.get_event_loop()
  File "/home/makcrx/anaconda3/lib/python3.10/site-packages/nest_asyncio.py", line 45, in _get_event_loop
    loop = events.get_event_loop_policy().get_event_loop()
  File "/home/makcrx/anaconda3/lib/python3.10/asyncio/events.py", line 671, in get_event_loop
    raise RuntimeError('There is no current event loop in thread %r.'
RuntimeError: There is no current event loop in thread 'Thread-9 (run)'.

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/home/makcrx/anaconda3/lib/python3.10/threading.py", line 1016, in _bootstrap_inner
    self.run()
  File "/home/makcrx/anaconda3/lib/python3.10/threading.py", line 953, in run
    self._target(*self._args, **self._kwargs)
  File "/home/makcrx/anaconda3/lib/python3.10/site-packages/u